# Convert Series to Rates per 100,000

In [1]:
import pandas as pd
import os

In [2]:
ts_folder = "../../data/covid-19_jhu-csse/"
wb_path = "../../data/worldbank/SP.POP.TOTL.zip"
geodata_path = "../../data/geodata/geo_data.csv"
out_folder = None
PAPERMILL_OUTPUT_PATH = None

In [3]:
# Parameters
PAPERMILL_INPUT_PATH = "notebooks/process/ToRates.ipynb"
PAPERMILL_OUTPUT_PATH = "runs/ToRates.run.ipynb"
ts_folder = "./data/covid-19_jhu-csse/"
wb_path = "./data/worldbank/SP.POP.TOTL.zip"
geodata_path = "./data/geodata/geo_data.csv"
out_folder = "./data/covid-19_rates/"


## Read in JHU CSSE data

I will switch to [xarray](http://xarray.pydata.org/en/stable/), but ATM, it's easier like this...

In [4]:
def read_jhu_covid_region_df(name):
    filename = os.path.join(ts_folder, f"time_series_covid19_{name}_global.csv")
    df = pd.read_csv(filename)
    df = df.set_index(['Country/Region', 'Province/State', 'Lat', 'Long'])
    df.columns = pd.to_datetime(df.columns)
    region_df = df.groupby(level='Country/Region').sum()
    loc_df = df.reset_index([2,3]).groupby(level='Country/Region').mean()[['Long', 'Lat']]
    return region_df.join(loc_df).set_index(['Long', 'Lat'], append=True)

In [5]:
frames_map = {
    "confirmed": read_jhu_covid_region_df("confirmed"),
    "deaths": read_jhu_covid_region_df("deaths"),
}

# Read in World Bank data

In [6]:
import zipfile
zf = zipfile.ZipFile(wb_path)
pop_df = pd.read_csv(zf.open("API_SP.POP.TOTL_DS2_en_csv_v2_821007.csv"), skiprows=4)

There is 2018 pop data for all countries/regions except Eritrea

In [7]:
pop_df[pd.isna(pop_df['2018'])]

Country Name Country Code     Indicator Name Indicator Code       1960  \
67          Eritrea          ERI  Population, total    SP.POP.TOTL  1007590.0   
108  Not classified          INX  Population, total    SP.POP.TOTL        NaN   

          1961       1962       1963       1964       1965  ...       2011  \
67   1033328.0  1060486.0  1088854.0  1118159.0  1148189.0  ...  3213972.0   
108        NaN        NaN        NaN        NaN        NaN  ...        NaN   

     2012  2013  2014  2015  2016  2017  2018  2019  Unnamed: 64  
67    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN          NaN  
108   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN          NaN  

[2 rows x 65 columns]

Fix the country/region names that differ between the World Bank population data and the JHU CSSE data.

In [8]:
region_wb_jhu_map = {
     'Brunei Darussalam': 'Brunei',
     'Czech Republic': 'Czechia',
     'Egypt, Arab Rep.': 'Egypt',
     'Hong Kong SAR, China': 'Hong Kong SAR',
     'Iran, Islamic Rep.': 'Iran',
     'Korea, Rep.': 'Korea, South',
     'Macao SAR, China': 'Macao SAR',
     'Russian Federation': 'Russia',
     'Slovak Republic': 'Slovakia',
     'St. Martin (French part)': 'Saint Martin',
     'United States': 'US'
}
current_pop_ser = pop_df[['Country Name', '2018']].copy().replace(region_wb_jhu_map).set_index('Country Name')['2018']
data_pop_ser = current_pop_ser[current_pop_ser.index.isin(frames_map['confirmed'].index.levels[0])]

In [9]:
# Use this to find the name in the series
# current_pop_ser[current_pop_ser.index.str.contains('Czech')]

There are some regions that we cannot resolve, but we will just ignore these.

In [10]:
frames_map['confirmed'].loc[
    frames_map['confirmed'].index.levels[0].isin(data_pop_ser.index) == False
].iloc[:,-2:]

2020-03-28 00:00:00  \
Country/Region                   Long        Lat                               
Bahamas                          -77.396300   25.034300                   10   
Burma                             95.956000   21.916200                    8   
Congo (Brazzaville)               21.758700  -4.038300                     4   
Congo (Kinshasa)                  21.758700  -4.038300                    65   
Diamond Princess                  0.000000    0.000000                   712   
Gambia                           -15.310100   13.443200                    3   
Holy See                          12.453400   41.902900                    6   
Kyrgyzstan                        74.766100   41.204400                   58   
Laos                              102.495496  19.856270                    8   
MS Zaandam                        0.000000    0.000000                     2   
Saint Kitts and Nevis            -62.782998   17.357822                    2   
Saint Lucia                      -60.978900   13.909400                    3   
Saint Vincent and the Grenadines -61.287200   12.984300                    1   
Syria                             38.996815   34.802075                    5   
Taiwan*                           121.000000  23.700000                  283   
Venezuela                        -66.589700   6.423800                   119   

                                                         2020-03-29 00:00:00  
Country/Region                   Long        Lat                              
Bahamas                          -77.396300   25.034300                   11  
Burma                             95.956000   21.916200                   10  
Congo (Brazzaville)               21.758700  -4.038300                    19  
Congo (Kinshasa)                  21.758700  -4.038300                    65  
Diamond Princess                  0.000000    0.000000                   712  
Gambia                           -15.310100   13.443200                    4  
Holy See                          12.453400   41.902900                    6  
Kyrgyzstan                        74.766100   41.204400                   84  
Laos                              102.495496  19.856270                    8  
MS Zaandam                        0.000000    0.000000                     2  
Saint Kitts and Nevis            -62.782998   17.357822                    2  
Saint Lucia                      -60.978900   13.909400                    9  
Saint Vincent and the Grenadines -61.287200   12.984300                    1  
Syria                             38.996815   34.802075                    9  
Taiwan*                           121.000000  23.700000                  298  
Venezuela                        -66.589700   6.423800                   119

# Read in geodata to get additional population numbers

In [11]:
geodata_df = pd.read_csv(geodata_path).drop('Unnamed: 0', axis=1).set_index('name_jhu')

Add in populations for missing countries

In [12]:
missing_countries = frames_map['confirmed'].loc[
    frames_map['confirmed'].index.levels[0].isin(data_pop_ser.index) == False
].iloc[:,-2:].reset_index()['Country/Region']

display(geodata_df.loc[geodata_df.index.isin(missing_countries)])

data_pop_ser = data_pop_ser.append(geodata_df.loc[geodata_df.index.isin(missing_countries), 'pop_est'])

name  \
name_jhu                                                
Bahamas                                       Bahamas   
Kyrgyzstan                                 Kyrgyzstan   
Saint Kitts and Nevis             St. Kitts and Nevis   
Saint Lucia                               Saint Lucia   
Syria                                           Syria   
Taiwan*                                        Taiwan   
Saint Vincent and the Grenadines   St. Vin. and Gren.   
Venezuela                                   Venezuela   

                                                         name_long region_un  \
name_jhu                                                                       
Bahamas                                                    Bahamas  Americas   
Kyrgyzstan                                              Kyrgyzstan      Asia   
Saint Kitts and Nevis                        Saint Kitts and Nevis  Americas   
Saint Lucia                                            Saint Lucia  Americas   
Syria                                                        Syria      Asia   
Taiwan*                                                     Taiwan      Asia   
Saint Vincent and the Grenadines  Saint Vincent and the Grenadines  Americas   
Venezuela                                                Venezuela  Americas   

                                      subregion                   region_wb  \
name_jhu                                                                      
Bahamas                               Caribbean   Latin America & Caribbean   
Kyrgyzstan                         Central Asia       Europe & Central Asia   
Saint Kitts and Nevis                 Caribbean   Latin America & Caribbean   
Saint Lucia                           Caribbean   Latin America & Caribbean   
Syria                              Western Asia  Middle East & North Africa   
Taiwan*                            Eastern Asia         East Asia & Pacific   
Saint Vincent and the Grenadines      Caribbean   Latin America & Caribbean   
Venezuela                         South America   Latin America & Caribbean   

                                   pop_est  gdp_md_est  \
name_jhu                                                 
Bahamas                             309156      9093.0   
Kyrgyzstan                         5431747     11610.0   
Saint Kitts and Nevis                40131       777.7   
Saint Lucia                         160267      1778.0   
Syria                             20178485     98830.0   
Taiwan*                           22974347    712000.0   
Saint Vincent and the Grenadines    104574      1070.0   
Venezuela                         26814843    357400.0   

                                               income_grp   Longitude  \
name_jhu                                                                
Bahamas                           2. High income: nonOECD  -76.628430   
Kyrgyzstan                                  5. Low income   74.541655   
Saint Kitts and Nevis             2. High income: nonOECD  -62.687553   
Saint Lucia                        3. Upper middle income  -60.969699   
Syria                              4. Lower middle income   38.507882   
Taiwan*                           2. High income: nonOECD  120.954273   
Saint Vincent and the Grenadines   3. Upper middle income  -61.201297   
Venezuela                          3. Upper middle income  -66.181841   

                                   Latitude  
name_jhu                                     
Bahamas                           24.290367  
Kyrgyzstan                        41.462219  
Saint Kitts and Nevis             17.264599  
Saint Lucia                       13.894795  
Syria                             35.025474  
Taiwan*                           23.753993  
Saint Vincent and the Grenadines  13.224723  
Venezuela                          7.124224

# Compute rates per 100,000 for regions

In [13]:
def cases_to_rates_df(df):
    per_100000_df = df.reset_index([1, 2], drop=True)
    per_100000_df = per_100000_df.div(data_pop_ser, 'index').mul(100000).dropna()
    per_100000_df.index.name = 'Country/Region'
    return per_100000_df
    
def frames_to_rates(frames_map):
    return {k: cases_to_rates_df(v) for k,v in frames_map.items()}


rates_map = frames_to_rates(frames_map)

In [14]:
if PAPERMILL_OUTPUT_PATH:
    for k, v in rates_map.items():
        out_path = os.path.join(out_folder, f"ts_rates_19-covid-{k}.csv")
        v.reset_index().to_csv(out_path)